In [1]:
using JuMP, MosekTools

In [2]:
import CSV
import DataFrames

In [3]:
csv_df = CSV.read("data.csv", DataFrames.DataFrame)

741×105 DataFrame
 Row │ Column1                     total_points  element_type  now_cost  team  ⋯
     │ String                      Int64         String3       Int64     Strin ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ Aaron Connolly                         5  FWD                 53  Brigh ⋯
   2 │ Aaron Cresswell                      115  DEF                 54  West
   3 │ Aaron Lennon                          60  MID                 46  Burnl
   4 │ Aaron Ramsdale                       135  GK                  51  Arsen
   5 │ Aaron Ramsey                           0  MID                 44  Aston ⋯
   6 │ Aaron Wan-Bissaka                     41  DEF                 51  Man U
   7 │ Abdoulaye Doucouré                    90  MID                 53  Evert
   8 │ Abu Kamara                             0  FWD                 45  Norwi
   9 │ Adam Armstrong                        57  FWD                 57  South ⋯
  10 │ Adam Forshaw                          38  MID                 45  Leeds
  11 │ Adam Idah                             36  FWD                 48  Norwi
  ⋮  │             ⋮                    ⋮             ⋮           ⋮            ⋱
 732 │ Youri Tielemans                      120  MID                 64  Leice
 733 │ Yves Bissouma                         66  MID                 44  Brigh ⋯
 734 │ Zach Awe                               0  DEF                 40  Arsen
 735 │ Zack Steffen                           7  GK                  44  Man C
 736 │ Zak Swanson                            0  DEF                 40  Arsen
 737 │ Álvaro Fernández                      31  GK                  45  Man U ⋯
 738 │ Álvaro Fernández                      31  GK                  45  Brent
 739 │ Álvaro Fernández                       0  DEF                 40  Man U
 740 │ Álvaro Fernández                       0  DEF                 40  Brent
 741 │ Çaglar Söyüncü                        66  DEF                 49  Leice ⋯
                                                101 columns and 720 rows omitted

In [4]:
total_points = csv_df[:, "total_points"]
cost = csv_df[:, "now_cost"]

gk = csv_df[:, "GK"]
def = csv_df[:, "DEF"]
fwd = csv_df[:, "FWD"]
mid = csv_df[:, "MID"]

club_df = csv_df[:, 6:6+19]
club = Matrix(club_df)

#print(total_points, fwd, mid)
club_df

741×20 DataFrame
 Row │ Arsenal  Aston Villa  Brentford  Brighton  Burnley  Chelsea  Crystal Pa ⋯
     │ Int64    Int64        Int64      Int64     Int64    Int64    Int64      ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │       0            0          0         1        0        0             ⋯
   2 │       0            0          0         0        0        0
   3 │       0            0          0         0        1        0
   4 │       1            0          0         0        0        0
   5 │       0            1          0         0        0        0             ⋯
   6 │       0            0          0         0        0        0
   7 │       0            0          0         0        0        0
   8 │       0            0          0         0        0        0
   9 │       0            0          0         0        0        0             ⋯
  10 │       0            0          0         0        0        0
  11 │       0            0          0         0        0        0
  ⋮  │    ⋮          ⋮           ⋮         ⋮         ⋮        ⋮           ⋮    ⋱
 732 │       0            0          0         0        0        0
 733 │       0            0          0         1        0        0             ⋯
 734 │       1            0          0         0        0        0
 735 │       0            0          0         0        0        0
 736 │       1            0          0         0        0        0
 737 │       0            0          0         0        0        0             ⋯
 738 │       0            0          1         0        0        0
 739 │       0            0          0         0        0        0
 740 │       0            0          1         0        0        0
 741 │       0            0          0         0        0        0             ⋯
                                                 14 columns and 720 rows omitted

In [5]:
points_df = csv_df[:, 7+19+4:7+19+4+37]
points = Matrix(points_df)
points_df

741×38 DataFrame
 Row │ total_points week 1  total_points week 2  total_points week 3  total_po ⋯
     │ Float64              Float64              Float64              Float64  ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │                 0.0                  1.0                  0.0           ⋯
   2 │                 7.0                  2.0                  5.0
   3 │                 0.0                  0.0                  0.0
   4 │                 0.0                  0.0                  0.0
   5 │                 0.0                  0.0                  0.0           ⋯
   6 │                 2.0                  2.0                  8.0
   7 │                 8.0                  4.0                  3.0
   8 │                 0.0                  0.0                  0.0
   9 │                 6.0                  2.0                  5.0           ⋯
  10 │                 0.0                  0.0                  0.0
  11 │                 1.0                  0.0                  1.0
  ⋮  │          ⋮                    ⋮                    ⋮                    ⋱
 732 │                 3.0                  7.0                  2.0
 733 │                 2.0                  8.0                  1.0           ⋯
 734 │                 0.0                  0.0                  0.0
 735 │                 0.0                  0.0                  0.0
 736 │                 0.0                  0.0                  0.0
 737 │                 0.0                  0.0                  0.0           ⋯
 738 │                 0.0                  0.0                  0.0
 739 │                 0.0                  0.0                  0.0
 740 │                 0.0                  0.0                  0.0
 741 │                 6.0                  0.0                  2.0           ⋯
                                                 35 columns and 720 rows omitted

In [6]:
played_df = csv_df[:, 7+19+4+37+1:7+19+4+37*2+1]
played = Matrix(played_df)
played_df

741×38 DataFrame
 Row │ played week 1  played week 2  played week 3  played week 4  played week ⋯
     │ Float64        Float64        Float64        Float64        Float64     ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │           0.0            1.0            0.0            0.0            0 ⋯
   2 │           1.0            1.0            1.0            1.0            1
   3 │           0.0            0.0            1.0            1.0            0
   4 │           0.0            0.0            0.0            1.0            1
   5 │           0.0            0.0            0.0            0.0            0 ⋯
   6 │           1.0            1.0            1.0            1.0            1
   7 │           1.0            1.0            1.0            1.0            1
   8 │           0.0            0.0            0.0            0.0            0
   9 │           1.0            1.0            1.0            1.0            1 ⋯
  10 │           0.0            0.0            0.0            0.0            0
  11 │           1.0            0.0            1.0            1.0            1
  ⋮  │       ⋮              ⋮              ⋮              ⋮              ⋮     ⋱
 732 │           1.0            1.0            1.0            1.0            1
 733 │           1.0            1.0            1.0            1.0            1 ⋯
 734 │           0.0            0.0            0.0            0.0            0
 735 │           0.0            0.0            0.0            0.0            0
 736 │           0.0            0.0            0.0            0.0            0
 737 │           0.0            0.0            0.0            0.0            0 ⋯
 738 │           0.0            0.0            0.0            0.0            0
 739 │           0.0            0.0            0.0            0.0            0
 740 │           0.0            0.0            0.0            0.0            0
 741 │           1.0            1.0            1.0            1.0            1 ⋯
                                                 34 columns and 720 rows omitted

In [7]:
model = Model(Mosek.Optimizer)

A JuMP Model
Feasibility problem with:
Variables: 0
Model mode: AUTOMATIC
CachingOptimizer state: EMPTY_OPTIMIZER
Solver name: Mosek

In [8]:
n = length(cost) # no. of players
m = 38  # no. of game weeks

38

### Initialise variables

In [9]:
@variable(model, x[1:n, 1:m],Bin)
@variable(model, x2[1:n],Bin)
@variable(model, starter[1:n],Bin)

741-element Vector{VariableRef}:
 starter[1]
 starter[2]
 starter[3]
 starter[4]
 starter[5]
 starter[6]
 starter[7]
 starter[8]
 starter[9]
 starter[10]
 starter[11]
 starter[12]
 starter[13]
 ⋮
 starter[730]
 starter[731]
 starter[732]
 starter[733]
 starter[734]
 starter[735]
 starter[736]
 starter[737]
 starter[738]
 starter[739]
 starter[740]
 starter[741]

### Decision variables

In [10]:
@variable(model, delta[1:n],Bin)
@variable(model, gamma[1:n,1:m], Bin)
@variable(model, theta[1:n], Bin)

741-element Vector{VariableRef}:
 theta[1]
 theta[2]
 theta[3]
 theta[4]
 theta[5]
 theta[6]
 theta[7]
 theta[8]
 theta[9]
 theta[10]
 theta[11]
 theta[12]
 theta[13]
 ⋮
 theta[730]
 theta[731]
 theta[732]
 theta[733]
 theta[734]
 theta[735]
 theta[736]
 theta[737]
 theta[738]
 theta[739]
 theta[740]
 theta[741]

### No. of players per week constraint

In [11]:
@constraint(model, [j=1:m], sum(x[i,j] for i in 1:n) == 11)

38-element Vector{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.EqualTo{Float64}}, ScalarShape}}:
 x[1,1] + x[2,1] + x[3,1] + x[4,1] + x[5,1] + x[6,1] + x[7,1] + x[8,1] + x[9,1] + x[10,1] + x[11,1] + x[12,1] + x[13,1] + x[14,1] + x[15,1] + x[16,1] + x[17,1] + x[18,1] + x[19,1] + x[20,1] + x[21,1] + x[22,1] + x[23,1] + x[24,1] + x[25,1] + x[26,1] + x[27,1] + x[28,1] + x[29,1] + x[30,1] + x[31,1] + x[32,1] + x[33,1] + x[34,1] + x[35,1] + x[36,1] + x[37,1] + x[38,1] + x[39,1] + x[40,1] + x[41,1] + x[42,1] + x[43,1] + x[44,1] + x[45,1] + x[46,1] + x[47,1] + x[48,1] + x[49,1] + x[50,1] + x[51,1] + x[52,1] + x[53,1] + x[54,1] + x[55,1] + x[56,1] + x[57,1] + x[58,1] + x[59,1] + x[60,1] + x[61,1] + x[62,1] + x[63,1] + x[64,1] + x[65,1] + x[66,1] + x[67,1] + x[68,1] + x[69,1] + x[70,1] + x[71,1] + x[72,1] + x[73,1] + x[74,1] + x[75,1] + x[76,1] + x[77,1] + x[78,1] + x[79,1] + x[80,1] + x[81,1] + x[82,1] + x[83,1] + x[84,1]

### No. of players in fantasy lineup constraint

In [12]:
@constraint(model, sum(x2[i] for i in 1:n) == 15)

x2[1] + x2[2] + x2[3] + x2[4] + x2[5] + x2[6] + x2[7] + x2[8] + x2[9] + x2[10] + x2[11] + x2[12] + x2[13] + x2[14] + x2[15] + x2[16] + x2[17] + x2[18] + x2[19] + x2[20] + x2[21] + x2[22] + x2[23] + x2[24] + x2[25] + x2[26] + x2[27] + x2[28] + x2[29] + x2[30] + x2[31] + x2[32] + x2[33] + x2[34] + x2[35] + x2[36] + x2[37] + x2[38] + x2[39] + x2[40] + x2[41] + x2[42] + x2[43] + x2[44] + x2[45] + x2[46] + x2[47] + x2[48] + x2[49] + x2[50] + x2[51] + x2[52] + x2[53] + x2[54] + x2[55] + x2[56] + x2[57] + x2[58] + x2[59] + x2[60] + x2[61] + x2[62] + x2[63] + x2[64] + x2[65] + x2[66] + x2[67] + x2[68] + x2[69] + x2[70] + x2[71] + x2[72] + x2[73] + x2[74] + x2[75] + x2[76] + x2[77] + x2[78] + x2[79] + x2[80] + x2[81] + x2[82] + x2[83] + x2[84] + x2[85] + x2[86] + x2[87] + x2[88] + x2[89] + x2[90] + x2[91] + x2[92] + x2[93] + x2[94] + x2[95] + x2[96] + x2[97] + x2[98] + x2[99] + x2[100] + x2[101] + x2[102] + x2[103] + x2[104] + x2[105] + x2[106] + x2[107] + x2[108] + x2[109] + x2[110] + x2[111] 

In [13]:
# if player i plays in any week j, he is included in fantasy line up with x2[i] = 1
@constraint(model, [i=1:n], sum(x[i,j] for j in 1:m) <= m*(1-delta[i]))
@constraint(model, [i=1:n], x2[i] == 1-delta[i])

741-element Vector{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.EqualTo{Float64}}, ScalarShape}}:
 x2[1] + delta[1] == 1.0
 x2[2] + delta[2] == 1.0
 x2[3] + delta[3] == 1.0
 x2[4] + delta[4] == 1.0
 x2[5] + delta[5] == 1.0
 x2[6] + delta[6] == 1.0
 x2[7] + delta[7] == 1.0
 x2[8] + delta[8] == 1.0
 x2[9] + delta[9] == 1.0
 x2[10] + delta[10] == 1.0
 x2[11] + delta[11] == 1.0
 x2[12] + delta[12] == 1.0
 x2[13] + delta[13] == 1.0
 ⋮
 x2[730] + delta[730] == 1.0
 x2[731] + delta[731] == 1.0
 x2[732] + delta[732] == 1.0
 x2[733] + delta[733] == 1.0
 x2[734] + delta[734] == 1.0
 x2[735] + delta[735] == 1.0
 x2[736] + delta[736] == 1.0
 x2[737] + delta[737] == 1.0
 x2[738] + delta[738] == 1.0
 x2[739] + delta[739] == 1.0
 x2[740] + delta[740] == 1.0
 x2[741] + delta[741] == 1.0

### 11 starters and 4 subs constraint

In [14]:
@constraint(model, sum(starter[i] for i in 1:n) == 11)
#@constraint(model, sum(x2[i]*(1-starter[i]) for i in 1:n) == 4)

starter[1] + starter[2] + starter[3] + starter[4] + starter[5] + starter[6] + starter[7] + starter[8] + starter[9] + starter[10] + starter[11] + starter[12] + starter[13] + starter[14] + starter[15] + starter[16] + starter[17] + starter[18] + starter[19] + starter[20] + starter[21] + starter[22] + starter[23] + starter[24] + starter[25] + starter[26] + starter[27] + starter[28] + starter[29] + starter[30] + starter[31] + starter[32] + starter[33] + starter[34] + starter[35] + starter[36] + starter[37] + starter[38] + starter[39] + starter[40] + starter[41] + starter[42] + starter[43] + starter[44] + starter[45] + starter[46] + starter[47] + starter[48] + starter[49] + starter[50] + starter[51] + starter[52] + starter[53] + starter[54] + starter[55] + starter[56] + starter[57] + starter[58] + starter[59] + starter[60] + starter[61] + starter[62] + starter[63] + starter[64] + starter[65] + starter[66] + starter[67] + starter[68] + starter[69] + starter[70] + starter[71] + starter[72] + s

In [15]:
# starter must be part of 15 fantasy team
@constraint(model, [i=1:n], 1-x2[i] <= 1-theta[i])
@constraint(model, [i=1:n], starter[i] <= theta[i])

741-element Vector{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.LessThan{Float64}}, ScalarShape}}:
 starter[1] - theta[1] <= 0.0
 starter[2] - theta[2] <= 0.0
 starter[3] - theta[3] <= 0.0
 starter[4] - theta[4] <= 0.0
 starter[5] - theta[5] <= 0.0
 starter[6] - theta[6] <= 0.0
 starter[7] - theta[7] <= 0.0
 starter[8] - theta[8] <= 0.0
 starter[9] - theta[9] <= 0.0
 starter[10] - theta[10] <= 0.0
 starter[11] - theta[11] <= 0.0
 starter[12] - theta[12] <= 0.0
 starter[13] - theta[13] <= 0.0
 ⋮
 starter[730] - theta[730] <= 0.0
 starter[731] - theta[731] <= 0.0
 starter[732] - theta[732] <= 0.0
 starter[733] - theta[733] <= 0.0
 starter[734] - theta[734] <= 0.0
 starter[735] - theta[735] <= 0.0
 starter[736] - theta[736] <= 0.0
 starter[737] - theta[737] <= 0.0
 starter[738] - theta[738] <= 0.0
 starter[739] - theta[739] <= 0.0
 starter[740] - theta[740] <= 0.0
 starter[741] - theta[741] <= 0.0

### Only play subs if starters did not play that week constraint

In [16]:
# if starter played, must always include within the lineup
#@constraint(model, [i=1:n, j=1:m], x[i,j] >= played[i,j]*starter[i])

In [17]:
# if starter played, must always include within the lineup
@constraint(model, [i=1:n, j=1:m], played[i,j]*starter[i] <= gamma[i,j])
@constraint(model, [i=1:n, j=1:m], x[i,j] >= gamma[i,j])

741×38 Matrix{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.GreaterThan{Float64}}, ScalarShape}}:
 x[1,1] - gamma[1,1] >= 0.0      …  x[1,38] - gamma[1,38] >= 0.0
 x[2,1] - gamma[2,1] >= 0.0         x[2,38] - gamma[2,38] >= 0.0
 x[3,1] - gamma[3,1] >= 0.0         x[3,38] - gamma[3,38] >= 0.0
 x[4,1] - gamma[4,1] >= 0.0         x[4,38] - gamma[4,38] >= 0.0
 x[5,1] - gamma[5,1] >= 0.0         x[5,38] - gamma[5,38] >= 0.0
 x[6,1] - gamma[6,1] >= 0.0      …  x[6,38] - gamma[6,38] >= 0.0
 x[7,1] - gamma[7,1] >= 0.0         x[7,38] - gamma[7,38] >= 0.0
 x[8,1] - gamma[8,1] >= 0.0         x[8,38] - gamma[8,38] >= 0.0
 x[9,1] - gamma[9,1] >= 0.0         x[9,38] - gamma[9,38] >= 0.0
 x[10,1] - gamma[10,1] >= 0.0       x[10,38] - gamma[10,38] >= 0.0
 x[11,1] - gamma[11,1] >= 0.0    …  x[11,38] - gamma[11,38] >= 0.0
 x[12,1] - gamma[12,1] >= 0.0       x[12,38] - gamma[12,38] >= 0.0
 x[13,1] - gamma[13,1] >= 0.0       x[13,38

In [18]:
# if less than 11 starters played that week, num of subs can be more than 0
#@constraint(model, [j=1:m], 11 - sum(x[i,j]*starter[i] for i in 1:n) <= 11*(1-gamma[j]))
#@constraint(model, [j=1:m], sum(x[i,j]*(1-starter[i]) for i in 1:n) <= 4*(1-gamma[j]))

### Position constraints

15 overall fantasy squad constraint

In [19]:
@constraint(model, sum(gk[i] * x2[i] for i in 1:n) == 2)

x2[4] + x2[19] + x2[27] + x2[34] + x2[37] + x2[43] + x2[49] + x2[51] + x2[62] + x2[67] + x2[72] + x2[79] + x2[94] + x2[100] + x2[112] + x2[134] + x2[157] + x2[164] + x2[167] + x2[168] + x2[169] + x2[172] + x2[193] + x2[196] + x2[198] + x2[199] + x2[207] + x2[226] + x2[230] + x2[236] + x2[237] + x2[254] + x2[256] + x2[267] + x2[275] + x2[283] + x2[307] + x2[322] + x2[327] + x2[336] + x2[344] + x2[346] + x2[347] + x2[357] + x2[371] + x2[375] + x2[387] + x2[388] + x2[390] + x2[396] + x2[405] + x2[411] + x2[431] + x2[439] + x2[459] + x2[462] + x2[465] + x2[467] + x2[477] + x2[485] + x2[498] + x2[536] + x2[567] + x2[578] + x2[594] + x2[601] + x2[604] + x2[607] + x2[617] + x2[626] + x2[632] + x2[640] + x2[675] + x2[679] + x2[688] + x2[703] + x2[705] + x2[706] + x2[712] + x2[718] + x2[724] + x2[735] + x2[737] + x2[738] == 2.0

In [20]:
@constraint(model, sum(def[i] * x2[i] for i in 1:n) == 5)

x2[2] + x2[6] + x2[13] + x2[14] + x2[21] + x2[25] + x2[28] + x2[41] + x2[44] + x2[45] + x2[50] + x2[56] + x2[61] + x2[66] + x2[68] + x2[69] + x2[73] + x2[75] + x2[76] + x2[77] + x2[78] + x2[80] + x2[81] + x2[82] + x2[83] + x2[84] + x2[85] + x2[86] + x2[88] + x2[90] + x2[92] + x2[97] + x2[98] + x2[101] + x2[110] + x2[115] + x2[116] + x2[119] + x2[122] + x2[127] + x2[128] + x2[131] + x2[133] + x2[135] + x2[137] + x2[138] + x2[139] + x2[143] + x2[144] + x2[145] + x2[146] + x2[150] + x2[151] + x2[153] + x2[156] + x2[163] + x2[170] + x2[177] + x2[179] + x2[181] + x2[185] + x2[190] + x2[192] + x2[202] + x2[203] + x2[204] + x2[210] + x2[211] + x2[213] + x2[214] + x2[215] + x2[217] + x2[219] + x2[222] + x2[224] + x2[227] + x2[231] + x2[234] + x2[239] + x2[240] + x2[242] + x2[246] + x2[252] + x2[255] + x2[262] + x2[263] + x2[266] + x2[268] + x2[269] + x2[273] + x2[281] + x2[289] + x2[292] + x2[297] + x2[298] + x2[299] + x2[300] + x2[305] + x2[308] + x2[309] + x2[314] + x2[316] + x2[317] + x2[31

In [21]:
@constraint(model, sum(mid[i] * x2[i] for i in 1:n) == 5)

x2[3] + x2[5] + x2[7] + x2[10] + x2[12] + x2[15] + x2[17] + x2[18] + x2[20] + x2[22] + x2[23] + x2[24] + x2[26] + x2[29] + x2[31] + x2[32] + x2[33] + x2[35] + x2[38] + x2[42] + x2[46] + x2[47] + x2[48] + x2[52] + x2[53] + x2[54] + x2[57] + x2[58] + x2[60] + x2[65] + x2[70] + x2[71] + x2[74] + x2[87] + x2[89] + x2[91] + x2[93] + x2[95] + x2[96] + x2[99] + x2[102] + x2[103] + x2[104] + x2[105] + x2[106] + x2[107] + x2[108] + x2[113] + x2[117] + x2[118] + x2[120] + x2[123] + x2[126] + x2[129] + x2[130] + x2[132] + x2[136] + x2[140] + x2[141] + x2[142] + x2[148] + x2[149] + x2[152] + x2[154] + x2[158] + x2[159] + x2[160] + x2[166] + x2[171] + x2[173] + x2[174] + x2[175] + x2[176] + x2[178] + x2[180] + x2[183] + x2[186] + x2[187] + x2[189] + x2[191] + x2[195] + x2[200] + x2[205] + x2[206] + x2[209] + x2[212] + x2[218] + x2[220] + x2[223] + x2[225] + x2[232] + x2[233] + x2[235] + x2[238] + x2[243] + x2[244] + x2[245] + x2[247] + x2[248] + x2[250] + x2[251] + x2[257] + x2[258] + x2[259] + x2[

In [22]:
@constraint(model, sum(fwd[i] * x2[i] for i in 1:n) == 3)

x2[1] + x2[8] + x2[9] + x2[11] + x2[16] + x2[30] + x2[36] + x2[39] + x2[40] + x2[55] + x2[59] + x2[63] + x2[64] + x2[109] + x2[111] + x2[114] + x2[121] + x2[124] + x2[125] + x2[147] + x2[155] + x2[161] + x2[162] + x2[165] + x2[182] + x2[184] + x2[188] + x2[194] + x2[197] + x2[201] + x2[208] + x2[216] + x2[221] + x2[228] + x2[229] + x2[241] + x2[249] + x2[253] + x2[264] + x2[279] + x2[282] + x2[286] + x2[313] + x2[324] + x2[326] + x2[335] + x2[341] + x2[354] + x2[356] + x2[361] + x2[367] + x2[368] + x2[374] + x2[377] + x2[381] + x2[391] + x2[392] + x2[393] + x2[423] + x2[426] + x2[428] + x2[463] + x2[474] + x2[496] + x2[499] + x2[501] + x2[503] + x2[506] + x2[512] + x2[523] + x2[529] + x2[533] + x2[545] + x2[549] + x2[550] + x2[565] + x2[566] + x2[568] + x2[581] + x2[589] + x2[597] + x2[603] + x2[605] + x2[610] + x2[613] + x2[629] + x2[631] + x2[650] + x2[651] + x2[657] + x2[663] + x2[669] + x2[674] + x2[677] + x2[680] + x2[696] + x2[714] + x2[726] == 3.0

11 game week constraint and starter constraint

In [23]:
@constraint(model, [j=1:m], sum(gk[i]*x[i,j] for i in 1:n) == 1)
@constraint(model, sum(gk[i]*starter[i] for i in 1:n) == 1)

starter[4] + starter[19] + starter[27] + starter[34] + starter[37] + starter[43] + starter[49] + starter[51] + starter[62] + starter[67] + starter[72] + starter[79] + starter[94] + starter[100] + starter[112] + starter[134] + starter[157] + starter[164] + starter[167] + starter[168] + starter[169] + starter[172] + starter[193] + starter[196] + starter[198] + starter[199] + starter[207] + starter[226] + starter[230] + starter[236] + starter[237] + starter[254] + starter[256] + starter[267] + starter[275] + starter[283] + starter[307] + starter[322] + starter[327] + starter[336] + starter[344] + starter[346] + starter[347] + starter[357] + starter[371] + starter[375] + starter[387] + starter[388] + starter[390] + starter[396] + starter[405] + starter[411] + starter[431] + starter[439] + starter[459] + starter[462] + starter[465] + starter[467] + starter[477] + starter[485] + starter[498] + starter[536] + starter[567] + starter[578] + starter[594] + starter[601] + starter[604] + starter[6

In [24]:
@constraint(model, [j=1:m], sum(def[i]*x[i,j] for i in 1:n) >= 3)
@constraint(model, sum(def[i]*starter[i] for i in 1:n) >= 3)

starter[2] + starter[6] + starter[13] + starter[14] + starter[21] + starter[25] + starter[28] + starter[41] + starter[44] + starter[45] + starter[50] + starter[56] + starter[61] + starter[66] + starter[68] + starter[69] + starter[73] + starter[75] + starter[76] + starter[77] + starter[78] + starter[80] + starter[81] + starter[82] + starter[83] + starter[84] + starter[85] + starter[86] + starter[88] + starter[90] + starter[92] + starter[97] + starter[98] + starter[101] + starter[110] + starter[115] + starter[116] + starter[119] + starter[122] + starter[127] + starter[128] + starter[131] + starter[133] + starter[135] + starter[137] + starter[138] + starter[139] + starter[143] + starter[144] + starter[145] + starter[146] + starter[150] + starter[151] + starter[153] + starter[156] + starter[163] + starter[170] + starter[177] + starter[179] + starter[181] + starter[185] + starter[190] + starter[192] + starter[202] + starter[203] + starter[204] + starter[210] + starter[211] + starter[213] + 

In [25]:
@constraint(model, [j=1:m], sum(fwd[i]*x[i,j] for i in 1:n) >= 1)
@constraint(model, sum(fwd[i]*starter[i] for i in 1:n) >= 1)

starter[1] + starter[8] + starter[9] + starter[11] + starter[16] + starter[30] + starter[36] + starter[39] + starter[40] + starter[55] + starter[59] + starter[63] + starter[64] + starter[109] + starter[111] + starter[114] + starter[121] + starter[124] + starter[125] + starter[147] + starter[155] + starter[161] + starter[162] + starter[165] + starter[182] + starter[184] + starter[188] + starter[194] + starter[197] + starter[201] + starter[208] + starter[216] + starter[221] + starter[228] + starter[229] + starter[241] + starter[249] + starter[253] + starter[264] + starter[279] + starter[282] + starter[286] + starter[313] + starter[324] + starter[326] + starter[335] + starter[341] + starter[354] + starter[356] + starter[361] + starter[367] + starter[368] + starter[374] + starter[377] + starter[381] + starter[391] + starter[392] + starter[393] + starter[423] + starter[426] + starter[428] + starter[463] + starter[474] + starter[496] + starter[499] + starter[501] + starter[503] + starter[506

### Cost constraint

In [26]:
@constraint(model, sum(cost[i] * x2[i] for i in 1:n) <= 1000)

53 x2[1] + 54 x2[2] + 46 x2[3] + 51 x2[4] + 44 x2[5] + 51 x2[6] + 53 x2[7] + 45 x2[8] + 57 x2[9] + 45 x2[10] + 48 x2[11] + 53 x2[12] + 43 x2[13] + 43 x2[14] + 56 x2[15] + 45 x2[16] + 59 x2[17] + 45 x2[18] + 43 x2[19] + 52 x2[20] + 40 x2[21] + 48 x2[22] + 45 x2[23] + 58 x2[24] + 40 x2[25] + 44 x2[26] + 43 x2[27] + 49 x2[28] + 58 x2[29] + 81 x2[30] + 51 x2[31] + 45 x2[32] + 55 x2[33] + 61 x2[34] + 43 x2[35] + 67 x2[36] + 47 x2[37] + 50 x2[38] + 45 x2[39] + 54 x2[40] + 46 x2[41] + 50 x2[42] + 39 x2[43] + 39 x2[44] + 73 x2[45] + 50 x2[46] + 52 x2[47] + 49 x2[48] + 39 x2[49] + 49 x2[50] + 40 x2[51] + 48 x2[52] + 47 x2[53] + 45 x2[54] + 76 x2[55] + 61 x2[56] + 56 x2[57] + 45 x2[58] + 53 x2[59] + 44 x2[60] + 44 x2[61] + 39 x2[62] + 52 x2[63] + 48 x2[64] + 52 x2[65] + 47 x2[66] + 40 x2[67] + 44 x2[68] + 60 x2[69] + 45 x2[70] + 57 x2[71] + 45 x2[72] + 39 x2[73] + 62 x2[74] + 40 x2[75] + 40 x2[76] + 45 x2[77] + 45 x2[78] + 42 x2[79] + 44 x2[80] + 47 x2[81] + 39 x2[82] + 46 x2[83] + 40 x2[84] + 4

### No. of players from same club constraint

In [27]:
@constraint(model, [c=1:20], sum(club[i,c] * x2[i] for i in 1:n) .<= 3)

20-element Vector{ConstraintRef{Model, MathOptInterface.ConstraintIndex{MathOptInterface.ScalarAffineFunction{Float64}, MathOptInterface.LessThan{Float64}}, ScalarShape}}:
 x2[4] + x2[20] + x2[22] + x2[25] + x2[30] + x2[62] + x2[85] + x2[94] + x2[107] + x2[117] + x2[150] + x2[197] + x2[205] + x2[229] + x2[242] + x2[243] + x2[245] + x2[268] + x2[388] + x2[402] + x2[406] + x2[435] + x2[458] + x2[469] + x2[490] + x2[495] + x2[505] + x2[506] + x2[509] + x2[538] + x2[542] + x2[551] + x2[561] + x2[581] + x2[593] + x2[600] + x2[618] + x2[626] + x2[628] + x2[642] + x2[661] + x2[676] + x2[719] + x2[722] + x2[734] + x2[736] <= 3.0
 x2[5] + x2[66] + x2[89] + x2[95] + x2[97] + x2[110] + x2[111] + x2[113] + x2[142] + x2[162] + x2[187] + x2[206] + x2[207] + x2[217] + x2[226] + x2[240] + x2[291] + x2[293] + x2[327] + x2[343] + x2[365] + x2[384] + x2[392] + x2[408] + x2[416] + x2[420] + x2[433] + x2[449] + x2[470] + x2[484] + x2[496] + x2[515] + x2[550] + x2[577] + x2[607] + x2[678] + x2[690] + x2[702

In [28]:
@objective(model, Max, sum(points[i,j] * x[i,j] for i in 1:n, j in 1:m))

x[1,2] + x[1,6] + x[1,15] + 2 x[1,17] + 7 x[2,1] + 2 x[2,2] + 5 x[2,3] + 8 x[2,4] + x[2,5] + 2 x[2,6] + x[2,7] + 7 x[2,8] + 12 x[2,9] + 2 x[2,10] + x[2,11] + 2 x[2,12] + 2 x[2,13] + 6 x[2,22] + 2 x[2,23] + 8 x[2,24] + 8 x[2,26] + 7 x[2,27] + 2 x[2,28] + x[2,29] + x[2,30] + 9 x[2,31] + x[2,32] + 2 x[2,33] + 2 x[2,34] + 6 x[2,36] + x[2,37] + x[2,38] + x[3,4] + x[3,6] + x[3,7] + x[3,14] + x[3,16] + 7 x[3,20] + 2 x[3,21] + 3 x[3,23] + x[3,24] + 2 x[3,25] + 8 x[3,26] + 5 x[3,27] + 2 x[3,28] + 2 x[3,29] + 2 x[3,31] + 2 x[3,32] + x[3,34] + 2 x[3,35] + 2 x[3,36] + x[3,37] + x[3,38] + 6 x[4,4] + 9 x[4,5] + 3 x[4,6] + 6 x[4,7] + 2 x[4,8] + 3 x[4,9] + 10 x[4,10] + 7 x[4,11] + x[4,12] + 7 x[4,13] + 3 x[4,14] + 2 x[4,15] + 11 x[4,16] + 5 x[4,17] + 2 x[4,18] + 6 x[4,19] + x[4,21] + 8 x[4,23] + 9 x[4,24] + 2 x[4,26] + 2 x[4,28] + 9 x[4,29] + x[4,31] + x[4,32] + 2 x[4,33] + 3 x[4,34] + 2 x[4,35] + 2 x[4,36] + 2 x[4,37] + 2 x[4,38] + 2 x[6,1] + 2 x[6,2] + 8 x[6,3] + 2 x[6,4] + 2 x[6,5] + 2 x[6,6] + 2 x

In [29]:
print(model)

In [ ]:
optimize!(model)

Problem
  Name                   :                 
  Objective sense        : maximize        
  Type                   : LO (linear optimization problem)
  Constraints            : 118742          
  Affine conic cons.     : 0               
  Disjunctive cons.      : 0               
  Cones                  : 0               
  Scalar variables       : 59280           
  Matrix variables       : 0               
  Integer variables      : 59280           

Optimizer started.
Mixed integer optimizer started.
Threads used: 4
Presolve started.
Presolve terminated. Time = 0.51, probing time =  0.06
Presolved problem: 29640 variables, 11351 constraints, 98466 non-zeros
Presolved problem: 0 general integer, 29640 binary, 0 continuous
Clique table size: 38625
BRANCHES RELAXS   ACT_NDS  DEPTH    BEST_INT_OBJ         BEST_RELAX_OBJ       REL_GAP(%)  TIME  
0        0        1        0        5.2000000000e+02     NA                   NA          0.8   
0        1        1        0        5.2

In [ ]:
starting_11 = value.(x2)
starting_11

In [ ]:
objective_value(model)

In [ ]:
csv_df[!, "Starting 11"] = value.(starter)
csv_df[!, "Fantasy lineup"] = value.(x2)

In [ ]:
csv_df

In [ ]:
CSV.write("results.csv", csv_df)

In [ ]:
using DataFrames

In [ ]:
xij_df = DataFrame(value.(x), :auto)

In [ ]:
xij_df[!, "Name"] = csv_df[1:n, "Column1"]
xij_df[!, "Team"] = csv_df[1:n, "team"]
xij_df[!, "Position"] = csv_df[1:n, "element_type"]
xij_df

In [ ]:
xij_df[!, "Starting 11"] = value.(starter)
xij_df[!, "Fantasy lineup"] = value.(x2)
xij_df

In [ ]:
CSV.write("Xij.csv", xij_df)